# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Homework 6

In [ ]:
# Load the necessary packages for this assignment.
# LinearAlgebra provides matrix and vector operations.
# Plots is used for data visualization.
using LinearAlgebra, Plots

### Problem 1: The Ill-Conditioned Hilbert Matrix

A *Hilbert matrix* $H$ is a classic example in numerical linear algebra. Its entries are defined by the formula:

$$ H_{ij} = \frac{1}{i + j - 1} $$

Despite their simple definition, Hilbert matrices are notoriously **ill-conditioned**, meaning that small numerical errors can be greatly amplified when performing computations with them. Let's explore this property.

#### 1a: Constructing the Hilbert Matrix

First, create a 2D array representing a $6 \times 6$ Hilbert matrix.

#### 1b: Leveraging Symmetry

Notice that $H_{ij} = H_{ji}$. This means $H$ is a **symmetric** matrix. We can inform Julia of this property to enable more efficient, specialized algorithms for symmetric matrices.

#### 1c: Squaring the Matrix

Now, let's compute the matrix $G = H^2 = H \times H$.

#### 1d: Defining a Linear System

Consider the linear system $G\boldsymbol{x} = \boldsymbol{b}$, where each element $b_i$ of the vector $\boldsymbol{b}$ is the sum of the elements in the $i$-th row of $G$:

$$ b_i = \sum_{j=1}^n G_{ij} $$

Given this definition of $\boldsymbol{b}$, what is the exact solution $\boldsymbol{x}$?

_**Solution:**_ 

#### 1e: Numerical Solution

Let's solve for $\boldsymbol{x}$ numerically using Julia and see how close our computed solution is to the exact one.

#### 1f: Calculating the Error

To see the impact of the matrix's ill-conditioning, compute the error between our numerical solution $\boldsymbol{x}$ and the exact solution $\boldsymbol{1}$ (a vector of all ones). We'll measure the error using the Euclidean norm, $\| \boldsymbol{x} - \boldsymbol{1} \|_2$.

#### 1g: The Condition Number

The error we see is due to the matrix $G$ being highly **ill-conditioned**. A measure of this is the *condition number*, which is the ratio of the largest to the smallest eigenvalue (for a symmetric matrix).

$$ \kappa(G) = \frac{\lambda_\mathrm{max}}{\lambda_\mathrm{min}} $$

A large condition number means the matrix is close to being singular, and numerical solutions of systems involving it are very sensitive to small errors. Let's compute it for $G$.

### Problem 2: Strassen's Divide-and-Conquer Matrix Multiplication

The **Strassen algorithm** is a recursive method for matrix multiplication that is asymptotically faster than the standard algorithm. For large matrices, it has a theoretical complexity of approximately $O(n^{\log_2 7}) \approx O(n^{2.807})$, which beats the standard $O(n^3)$ complexity.

The trick is to reduce the number of required multiplications from 8 to 7 at each step of the recursion. For two $n \times n$ matrices $A$ and $B$ (where $n$ is a power of 2), we partition them into four $n/2 \times n/2$ sub-matrices:

$$ A = \begin{pmatrix} A_{11} & A_{12} \\ A_{21} & A_{22} \end{pmatrix}, \quad B = \begin{pmatrix} B_{11} & B_{12} \\ B_{21} & B_{22} \end{pmatrix}, \quad C = \begin{pmatrix} C_{11} & C_{12} \\ C_{21} & C_{22} \end{pmatrix} $$

We then compute 7 sub-products, $M_1$ through $M_7$, recursively:
$$ \begin{align*} M_1 &= (A_{11} + A_{22})(B_{11} + B_{22}) \\ M_2 &= (A_{21} + A_{22})B_{11} \\ M_3 &= A_{11}(B_{12} - B_{22}) \\ M_4 &= A_{22}(B_{21} - B_{11}) \\ M_5 &= (A_{11} + A_{12})B_{22} \\ M_6 &= (A_{21} - A_{11})(B_{11} + B_{12}) \\ M_7 &= (A_{12} - A_{22})(B_{21} + B_{22}) \end{align*} $$

Finally, the sub-matrices of the result $C$ are formed by additions and subtractions of the $M_i$ matrices:

$$ \begin{align*} C_{11} &= M_1 + M_4 - M_5 + M_7 \\ C_{12} &= M_3 + M_5 \\ C_{21} &= M_2 + M_4 \\ C_{22} &= M_1 - M_2 + M_3 + M_6 \end{align*} $$

Your task is to implement this algorithm in a function `strassen(A,B)`. The recursion should stop when the matrices are $1 \times 1$ (the base case), at which point you perform a simple scalar multiplication.

Let's test your function to make sure it produces the correct result! We'll compare its output to Julia's built-in matrix multiplication.

In [ ]:
# Create two random 256x256 matrices (256 is a power of 2).
A = randn(256, 256)
B = randn(256, 256)

# Compute the product using your Strassen implementation.
C = strassen(A, B)

# Compute the product using Julia's standard, highly-optimized algorithm.
D = A * B

# Check the maximum absolute difference between the two results.
# This value should be very close to zero, accounting for floating-point inaccuracies.
maximum(abs.(C - D))

### Problem 3: Polynomial Curve Fitting

Let's generalize the linear regression example from lecture. Instead of fitting a line ($p=1$), we'll fit a polynomial of any degree $p \ge 1$ to a set of data points $(x_i, y_i)$.

The goal is to find the coefficients $c_0, c_1, \ldots, c_p$ of the polynomial
$$ P(x) = c_0 + c_1x + c_2x^2 + \cdots + c_px^p $$ 
that minimizes the sum of the squared errors between the polynomial and the data points. This is a classic least-squares problem.

#### 3a: The `polyfit` Function

Write a function `polyfit(x, y, p)` that takes data points `x` and `y` and a polynomial degree `p`, and returns the vector of best-fit coefficients.

**Hint:** This can be set up as a linear system $A\boldsymbol{c} = \boldsymbol{y}$, where $\boldsymbol{c}$ is the vector of unknown coefficients. The matrix $A$ is known as a **Vandermonde matrix**, where each row is of the form $[1, x_i, x_i^2, \ldots, x_i^p]$.

#### 3b: The `polyval` Function

Now, write a function `polyval(pol, xx)` that takes a vector of polynomial coefficients `pol` (as returned by `polyfit`) and a vector of x-values `xx`, and evaluates the polynomial at each of those points.

#### 3c: Putting It All Together

Use your functions to fit a cubic polynomial ($p=3$) to the noisy data below, and visualize the result in a way similar to the example in the lecture notebook.

In [ ]:
# Generate some sample data based on a cubic function with added random noise.
x = 0:0.1:10
noise = 2 * randn(size(x))
y = @. 0.1x^3 - x^2 + 2x - 2 + noise;

In [ ]:
# TODO: Fit cubic polynomial and visualize the result


### Problem 4: A Word Puzzle

Let's tackle a classic word puzzle from *Think Julia*:

> Give me a word with three consecutive double letters. I’ll give you a couple of words that
> almost qualify, but don’t. For example, the word committee, c-o-m-m-i-t-t-e-e. It would be
> great except for the i that sneaks in there. Or Mississippi: M-i-s-s-i-s-s-i-p-p-i. If you
> could take out those i’s it would work. But there is a word that has three consecutive pairs
> of letters and to the best of my knowledge this may be the only word. Of course there are
> probably 500 more but I can only think of one. What is the word?

Your task is to write a program that finds words with this pattern. First, download the file [words.txt](https://github.com/BenLauwens/ThinkJulia.jl/blob/master/data/words.txt). Then, place it in the same directory as this notebook. Your program should read the file line by line and print any word that contains three consecutive double letters (e.g., 'aa', 'bb', 'cc').